In [1]:
import pandas as pd
import scipy
import numpy as np
import pandas as pd
import matplotlib as mpl
from sklearn.model_selection import train_test_split
import copy

import gensim

In [2]:
data = pd.read_csv("data/train-balanced-sarcasm.csv")
data

label                                            comment  \
0            0                                         NC and NH.   
1            0  You do know west teams play against west teams...   
2            0  They were underdogs earlier today, but since G...   
3            0  This meme isn't funny none of the "new york ni...   
4            0                    I could use one of those tools.   
...        ...                                                ...   
1010821      1  I'm sure that Iran and N. Korea have the techn...   
1010822      1                 whatever you do, don't vote green!   
1010823      1  Perhaps this is an atheist conspiracy to make ...   
1010824      1  The Slavs got their own country - it is called...   
1010825      1  values, as in capitalism .. there is good mone...   

                 author           subreddit  score  ups  downs     date  \
0             Trumpbart            politics      2   -1     -1  2016-10   
1             Shbshb906                 nba     -4   -1     -1  2016-11   
2              Creepeth                 nfl      3    3      0  2016-09   
3             icebrotha  BlackPeopleTwitter     -8   -1     -1  2016-10   
4             cush2push  MaddenUltimateTeam      6   -1     -1  2016-12   
...                 ...                 ...    ...  ...    ...      ...   
1010821       TwarkMain          reddit.com      2    2      0  2009-04   
1010822        BCHarvey             climate      1    1      0  2009-05   
1010823  rebelcommander             atheism      1    1      0  2009-01   
1010824           catsi           worldnews      1    1      0  2009-01   
1010825        frogking            politics      2    2      0  2009-01   

                 created_utc  \
0        2016-10-16 23:55:23   
1        2016-11-01 00:24:10   
2        2016-09-22 21:45:37   
3        2016-10-18 21:03:47   
4        2016-12-30 17:00:13   
...                      ...   
1010821  2009-04-25 00:47:52   
1010822  2009-05-14 22:27:40   
1010823  2009-01-11 00:22:57   
1010824  2009-01-23 21:12:49   
1010825  2009-01-24 06:20:14   

                                            parent_comment  
0        Yeah, I get that argument. At this point, I'd ...  
1        The blazers and Mavericks (The wests 5 and 6 s...  
2                                  They're favored to win.  
3                               deadass don't kill my buzz  
4        Yep can confirm I saw the tool they use for th...  
...                                                    ...  
1010821  No one is calling this an engineered pathogen,...  
1010822  In a move typical of their recent do-nothing a...  
1010823  Screw the Disabled--I've got to get to Church ...  
1010824  I've always been unsettled by that. I hear a l...  
1010825  Why do the people who make our laws seem unabl...  

[1010826 rows x 10 columns]

In [3]:

s = data["comment"].isnull()
#s = reduced_weather["humidity"].isnull()
data_nan_list = s.index[s]
data_nan_list

Int64Index([  56269,   68590,  135348,  199910,  258718,  284331,  312969,
             328775,  331735,  332600,  332631,  362293,  389792,  445204,
             505371,  520619,  524263,  529336,  532823,  569280,  645450,
             651242,  661519,  675235,  683899,  747602,  799033,  800812,
             813274,  817886,  859333,  875251,  878050,  898863,  905291,
             914178,  914615,  918700,  919882,  923678,  936221,  949593,
             966886,  967116,  978220,  982492,  992907,  995023, 1001185,
            1001891, 1002133, 1009303, 1010599],
           dtype='int64')

In [4]:
data.dropna(subset=['comment', 'label'], inplace=True)

In [19]:
data

label                                            comment  \
0            0                                         NC and NH.   
1            0  You do know west teams play against west teams...   
2            0  They were underdogs earlier today, but since G...   
3            0  This meme isn't funny none of the "new york ni...   
4            0                    I could use one of those tools.   
...        ...                                                ...   
1010821      1  I'm sure that Iran and N. Korea have the techn...   
1010822      1                 whatever you do, don't vote green!   
1010823      1  Perhaps this is an atheist conspiracy to make ...   
1010824      1  The Slavs got their own country - it is called...   
1010825      1  values, as in capitalism .. there is good mone...   

                 author           subreddit  score  ups  downs     date  \
0             Trumpbart            politics      2   -1     -1  2016-10   
1             Shbshb906                 nba     -4   -1     -1  2016-11   
2              Creepeth                 nfl      3    3      0  2016-09   
3             icebrotha  BlackPeopleTwitter     -8   -1     -1  2016-10   
4             cush2push  MaddenUltimateTeam      6   -1     -1  2016-12   
...                 ...                 ...    ...  ...    ...      ...   
1010821       TwarkMain          reddit.com      2    2      0  2009-04   
1010822        BCHarvey             climate      1    1      0  2009-05   
1010823  rebelcommander             atheism      1    1      0  2009-01   
1010824           catsi           worldnews      1    1      0  2009-01   
1010825        frogking            politics      2    2      0  2009-01   

                 created_utc  \
0        2016-10-16 23:55:23   
1        2016-11-01 00:24:10   
2        2016-09-22 21:45:37   
3        2016-10-18 21:03:47   
4        2016-12-30 17:00:13   
...                      ...   
1010821  2009-04-25 00:47:52   
1010822  2009-05-14 22:27:40   
1010823  2009-01-11 00:22:57   
1010824  2009-01-23 21:12:49   
1010825  2009-01-24 06:20:14   

                                            parent_comment  
0        Yeah, I get that argument. At this point, I'd ...  
1        The blazers and Mavericks (The wests 5 and 6 s...  
2                                  They're favored to win.  
3                               deadass don't kill my buzz  
4        Yep can confirm I saw the tool they use for th...  
...                                                    ...  
1010821  No one is calling this an engineered pathogen,...  
1010822  In a move typical of their recent do-nothing a...  
1010823  Screw the Disabled--I've got to get to Church ...  
1010824  I've always been unsettled by that. I hear a l...  
1010825  Why do the people who make our laws seem unabl...  

[1010773 rows x 10 columns]

In [5]:

X_train, X_test, y_train, y_test = train_test_split(data["comment"],data["label"], test_size=0.2)

In [6]:
y_train

173115    0
494534    1
551789    1
993587    1
25324     1
         ..
423165    1
526380    0
135754    1
208892    0
864213    0
Name: label, Length: 808618, dtype: int64

In [11]:
X_train.index


Int64Index([173115, 494534, 551789, 993587,  25324, 136016,  74494, 798516,
            722210, 967947,
            ...
            174218, 333727, 731100, 678385, 605057, 423165, 526380, 135754,
            208892, 864213],
           dtype='int64', length=808618)

In [12]:
X_train[173115]

'Language censorship in media'

In [15]:
# size of the output vector
vec_size = 256

# function to preprocess and tokenize text
def tokenize_corpus(df, tokens_only=False):
    
    for i in df.index:
        line = df[i]
        tokens = gensim.utils.simple_preprocess(line)
        if tokens_only:
            yield tokens
        else:
            yield gensim.models.doc2vec.TaggedDocument(tokens, [i])
        print(f"{i}")

# tokenize a training corpus
corpus = list(tokenize_corpus(X_train))

# train doc2vec on the training corpus
model = gensim.models.doc2vec.Doc2Vec(vector_size=vec_size, min_count=2, epochs=40)
model.build_vocab(corpus)
model.train(corpus, total_examples=model.corpus_count, epochs=model.epochs)

# tokenize new documents
doc = list(tokenize_corpus(X_test, tokens_only=True))

# generate embeddings for the new documents
doc_emb = np.zeros((len(doc),vec_size))
for i in range(len(doc)):
    doc_emb[i,:] = model.infer_vector(doc[i])

173115
494534
551789
993587
25324
136016
74494
798516
722210
967947
218788
455655
159479
893899
899870
486758
9342
888636
617173
111577
24574
703974
829392
465621
48088
282046
711522
271178
624133
53830
190222
443433
701456
472958
724668
353387
654971
64644
765835
778842
238384
608442
308827
542155
827287
436205
390890
905322
385474
324012
792125
85566
423474
799332
309653
931993
807017
121344
501129
189608
119668
808205
159766
290267
249374
390802
49083
820643
950984
520154
24710
914440
87029
590082
917162
103897
609654
320052
13370
159930
81864
205349
283490
577243
129696
751720
321307
852619
548165
609231
502727
466410
147085
124375
858834
586581
559442
861766
207339
203755
1003180
290533
556195
455532
967056
169267
70023
280375
71661
711962
376014
621567
392716
728287
946399
683910
726360
614853
573971
369846
531610
52220
926805
439938
976343
126217
481712
703754
205046
25727
357923
220
723379
135217
842043
281926
787541
789778
531903
440270
233081
44117
554124
693063
988525
466875

637758
219351
158731
803285
641174
619193
875152
9186
400614
12769
802744
536988
398310
640684
34524
632688
511357
428114
378471
745410
824373
338206
140720
890657
248478
832737
160746
661351
580842
682880
737524
523276
249302
840121
941451
480127
264635
337731
591118
377885
866459
812690
952269
952520
605831
459423
941567
435121
803475
250073
450110
988260
216825
381787
204000
321737
170385
101213
682080
891925
497825
692550
659922
124846
128400
653060
940383
239144
763398
557621
229627
881362
552937
677509
165297
465034
524661
809599
674786
513953
941931
219078
818856
596261
607740
384216
94768
957091
916493
8170
261979
588931
15231
102088
256343
777644
108140
24284
970163
93079
591858
207086
946034
602174
402293
755349
655549
178115
104252
461882
616532
429186
339997
835941
914339
820711
858668
95908
209465
611475
443191
957564
176396
533199
929690
287457
556038
416025
117233
809396
180776
817166
589460
876956
297958
131270
245136
2366
142824
239037
177680
492647
469055
442680
77712

908823
148793
146911
21767
603383
899893
695939
528095
849883
523610
104141
891493
19273
949743
717227
680215
460697
987809
841654
675008
260683
801532
964681
394615
207325
18424
851360
468369
255992
528680
935416
167301
469396
867708
515307
570845
739904
765957
834629
232401
24817
308255
908908
19474
695560
997702
483987
962002
260063
507628
618265
999984
668711
537038
391377
834637
75132
335581
109665
879401
868480
64965
101085
50776
817429
540738
43679
572401
81118
89533
428121
338945
301330
555234
552109
776002
965940
614699
346325
772396
429836
616237
53337
608433
657847
416082
488132
687769
722322
542800
329381
257661
155946
600309
972792
640089
457917
135607
919221
561056
439005
993498
445711
941487
772427
144233
883379
228652
677455
752847
742942
270059
376851
891744
517006
190436
435303
493237
96552
683903
225556
734152
459994
495000
290852
680662
357877
337316
576025
719153
452148
941731
85488
725469
235086
579327
940374
84511
786575
528790
598465
642482
364109
850848
548421


371178
80771
872043
155605
315989
554542
893660
269072
238643
939779
914450
814926
859375
119058
807910
520188
719487
129491
739085
152198
113772
899290
204200
601121
638970
198727
160480
603600
421672
965540
709108
807892
689620
38266
759961
360942
273189
879751
12573
790713
421443
150986
257292
735665
646245
729924
905909
824957
88002
464869
969594
940150
72647
707289
628679
888278
214071
9747
74371
145171
851299
836172
414016
368940
514887
521352
55039
432903
770914
755073
80590
838883
460010
465350
428007
1000927
912314
475925
363969
898898
162621
810044
63032
614671
322163
963828
896936
354777
274286
225766
9501
496907
996462
738514
260359
116481
62406
196532
903624
485226
541145
413877
250578
479551
147252
298772
811012
27569
931378
828819
770986
621796
717281
785348
658169
61909
398821
127407
631946
546549
311849
279440
482985
116214
251890
108809
406743
379119
179024
431219
663223
976745
303822
341330
384544
459451
471452
688323
958991
75831
723537
6900
92995
743806
394670
2266

438604
361347
970827
129759
67245
662253
63520
907297
648949
607653
925854
100956
358787
350302
262828
16866
447625
288027
621271
510595
982647
169552
610035
585415
22168
945149
976646
837299
966019
755619
329657
32142
491762
807507
136953
631248
648093
551818
112373
779778
528546
42122
644755
851067
343999
414356
852128
455607
339339
460106
733541
127074
110588
356774
63887
897338
54145
671510
147753
1620
55438
71547
2050
919909
727512
915982
933340
408741
761185
338500
114736
808609
257165
771386
725143
61764
756366
421404
752119
402276
231080
276297
497574
413577
502866
875337
963138
199360
630211
173648
170378
305298
802023
821812
294046
873745
718645
814491
915074
308945
190008
394852
661159
56438
981347
667842
569021
410361
686992
194495
643062
280848
808756
625788
640504
60249
866054
286549
889119
674770
635367
883471
338532
447910
301078
163571
629528
936957
277620
942786
251919
573758
970627
863079
889215
681614
795594
991342
28770
708985
780570
242165
531240
988060
345535
529

...

583777
768456
874711
87013
125851
611953
80216
646612
79854
885165
100552
485535
347976
357660
472146
799107
186703
482681
337420
996719
171625
158730
36502
344238
246232
897796
474653
1003667
348174
332806
823568
362417
930610
171032
554917
783395
920673
990784
563765
812697
80092
734043
944269
1007974
283042
579138
143852
315924
431537
713055
747571
412479
212678
273724
605786
829176
140686
378111
255915
511183
676766
21103
615316
675535
645873
78716
668311
411972
854663
919294
484350
908829
688720
144191
820479
719303
297980
966495
475910
498272
868986
641882
940028
517970
3200
722141
741129
380696
267386
960218
24469
358418
535417
37995
940591
276347
439412
603557
315359
695733
576847
945545
701962
755981
741763
734419
752956
994553
127890
844415
12371
160581
72249
788310
520105
95889
429120
529366
1010568
619816
591636
504800
118050
836401
553578
587511
141961
177740
124280
302318
540509
404332
648211
747155
49830
379229
458341
336585
636609
1009780
628030
1006136
97687
389502
347

924620
35882
558479
813896
536669
171473
614493
630588
764325
343652
428458
857437
208935
568199
446592
328435
408828
422270
896522
517761
1007389
6951
661029
475728
350591
551917
958183
766836
658583
996168
114461
945947
10685
319971
495728
633418
133189
597610
637121
700821
567056
835137
941431
995318
446133
570324
651643
397641
423815
930425
833355
634576
130681
661271
231452
765059
21170
316615
356692
668397
681179
989392
448085
360371
362806
7050
102109
40476
428865
79590
581110
763818
180630
470101
935950
268318
79210
992651
273032
539630
45182
314502
793901
96566
107525
863027
844431
926654
710941
855294
213133
764582
881167
206422
926864
226163
355816
204308
652779
19715
669896
449764
214903
986463
332672
531944
128707
130454
144584
387361
964796
260847
792867
457786
697755
440428
190826
161598
232848
942310
643129
555397
611114
585552
1009661
730074
559781
808893
469940
5829
513438
938374
896963
535822
594481
99012
981076
720198
61430
739726
198415
108472
774963
569117
317296


659856
137757
476173
135786
90377
857977
452650
886412
90798
55153
648904
499354
94275
1004414
648608
616786
886382
56472
458134
437402
867218
497051
158138
745159
975868
652743
306236
1004384
760588
110884
750667
923604
746956
713311
340018
385038
251900
489996
933544
808388
309668
467588
118036
827403
678815
420380
38907
630288
760357
806542
286849
937764
548725
680691
72508
183627
665526
272317
844303
901664
216609
557240
440549
695080
358232
313644
499772
208822
484358
412694
811311
566246
514117
1002803
767568
263521
21791
57949
274264
938350
116858
818449
290431
379957
197024
930131
616606
751612
1003459
222258
739243
63734
691122
547825
943361
574482
479388
746841
903289
986950
692848
806710
559232
877822
493834
554675
342211
949366
662059
75600
320325
134207
527670
440063
575434
842985
574209
497094
264777
475996
60033
199099
90369
538290
861017
473849
480175
402061
731231
813586
897944
863011
679416
670290
237548
680913
937019
375989
761689
642998
985663
961807
701539
693147
6

78637
1004051
98917
668487
124669
600514
115689
789229
250471
332296
510323
51965
476591
75810
632962
229934
626902
788147
611635
160833
55312
46381
348948
411040
930871
246179
16653
573393
855415
493871
262927
978685
868112
47384
98569
871386
433908
38403
579980
692363
931787
850542
417883
360066
267490
490173
445662
658664
551623
630390
468048
316849
643456
890182
738452
724210
684997
576678
823189
449365
228166
977360
557520
342860
653574
927517
170588
166389
131807
469441
524144
677014
324828
89227
419808
140374
919092
427185
759027
582310
951147
440878
578969
491040
696045
746988
577001
410552
405977
780130
627199
737718
245692
761686
178090
248499
535072
437920
516847
391605
361403
751254
944993
832268
640330
390225
570106
200474


KeyboardInterrupt: 

In [14]:
doc_emb

array([[ 0.12266395, -0.27694765,  0.34945023, ..., -0.4977895 ,
        -0.0897756 ,  0.14064218],
       [ 0.57028639, -0.27474967, -0.21168599, ..., -0.21534806,
        -1.02002597,  0.92430258],
       [ 0.55598646, -0.31659195, -0.04713354, ..., -0.26520237,
        -0.95545977, -0.86877692],
       ...,
       [ 0.        ,  0.        ,  0.        , ...,  0.        ,
         0.        ,  0.        ],
       [ 0.        ,  0.        ,  0.        , ...,  0.        ,
         0.        ,  0.        ],
       [ 0.        ,  0.        ,  0.        , ...,  0.        ,
         0.        ,  0.        ]])

In [ ]:
import gensim

# size of the output vector
vec_size = 20

# function to preprocess and tokenize text
def tokenize_corpus(txt, tokens_only=False):
    for i, line in enumerate(txt):
        tokens = gensim.utils.simple_preprocess(line)
        if tokens_only:
            yield tokens
        else:
            yield gensim.models.doc2vec.TaggedDocument(tokens, [i])

# tokenize a training corpus
corpus = list(tokenize_corpus(train_corpus))

# train doc2vec on the training corpus
model = gensim.models.doc2vec.Doc2Vec(vector_size=vec_size, min_count=2, epochs=40)
model.build_vocab(corpus)
model.train(corpus, total_examples=model.corpus_count, epochs=model.epochs)

# tokenize new documents
doc = list(tokenize_corpus(test, tokens_only=True))

# generate embeddings for the new documents
doc_emb = np.zeros((len(doc),vec_size))
for i in range(len(doc)):
    doc_emb[i,:] = model.infer_vector(doc[i])